In [1]:
import numpy as np
import matplotlib.pyplot as plt
import json
import json
import os
import pandas as pd
import seaborn as sns
import glob
from natsort import natsorted
from scipy import stats
from sklearn.metrics import recall_score
from sklearn.metrics import auc as auc_score
from sklearn.metrics import roc_auc_score, roc_curve
sns.set(style="whitegrid")
import matplotlib as mpl
import torch
import torch.nn.functional as F
from sklearn.metrics import roc_auc_score
from matplotlib.ticker import PercentFormatter


In [2]:
import sys
sys.path.append('/home/colin/covid-blood/')
from config import get_config
from torchvision import transforms
from utils import setup_torch, get_covid_transforms, load_model
import wandb
from dataloader import load_all_patients, load_pbc_data
from models.imagenet import get_model
from models.multi_instance import AttentionModel, GatedAttentionModel, SimpleMIL
from mil_trainer import ClassificationTrainer
from torch import optim
import warnings
from tqdm import tqdm
import json

In [3]:
setup_torch(0, 1, 3)

In [4]:
cell_types = ['basophil', 'eosinophil', 'erythroblast', 'garbage', 'ig', 'lymphocyte', 'monocyte', 'neutrophil', 'platelet']
wbc_model = get_model('resnet50', len(cell_types), True).cuda()
wbc_model = load_model(wbc_model, '/home/colin/wbc_model_2021.pth').cuda()

In [5]:
data_transforms = get_covid_transforms(image_size=224, center_crop_amount=224)
train_loader, val_loader, test_loader = load_all_patients(train_transforms=data_transforms['train'],
                                                          test_transforms=data_transforms['val'],
                                                          batch_size=8,
                                                          fold_number=0,
                                                          group_by_patient=False,
                                                          weighted_sample=False,
                                                          random_sample=False,
                                                          extract_filenames=True)

156it [00:00, 8087.00it/s]
39it [00:00, 7819.96it/s]
39it [00:00, 7732.35it/s]

0.5 blank
reading cache


In [39]:
output_data = {}

In [40]:
with torch.no_grad():
    # load every image
    for loader in [train_loader, val_loader, test_loader]:
        print("Startnig loader")
        for (images, filenames), labels in loader:
            wbc_preds = wbc_model(images.cuda())
            for i in range(len(filenames)):
                order = os.path.basename(os.path.dirname(filenames[i]))
                filename = os.path.basename(filenames[i])
                if order not in output_data:
                    output_data[order] = {}
                preds = np.array(wbc_preds[i].cpu())
                output_data[order][filename] = {
                    'continous': np.array(wbc_preds[i].cpu()),
                    'discrete': np.argmax(preds),
                    'type': cell_types[np.argmax(preds)],
                    'label': int(labels[i])
                }
# predict the cell type (continous)
# save it for each order number, alongside outcome


Startnig loader
Startnig loader
Startnig loader


In [41]:
output_data['10051882383']

{'10051882383_094.jpg': {'continous': array([-4.2147284, -2.004626 , -2.2775476, -6.541765 , -1.8190163,
          1.9309133, -2.8141367, -4.7346196, -4.333583 ], dtype=float32),
  'discrete': 5,
  'type': 'lymphocyte',
  'label': 0},
 '10051882383_098.jpg': {'continous': array([-5.322716 , -0.9997605, -3.0168395, -5.828036 , -4.634687 ,
          2.1877596, -4.89258  , -5.9439874, -2.3288224], dtype=float32),
  'discrete': 5,
  'type': 'lymphocyte',
  'label': 0},
 '10051882383_097.jpg': {'continous': array([-3.4243913, -2.0335405, -1.756246 , -9.188159 , -3.622283 ,
          0.7689483, -5.4392805, -4.2861094, -3.9125662], dtype=float32),
  'discrete': 5,
  'type': 'lymphocyte',
  'label': 0},
 '10051882383_071.jpg': {'continous': array([-4.587863 , -4.0427146, -6.4468236, -6.4560804, -3.4911304,
         -2.8163357, -2.2970448, -0.9221369, -5.2645907], dtype=float32),
  'discrete': 7,
  'type': 'neutrophil',
  'label': 0},
 '10051882383_052.jpg': {'continous': array([-3.463202  , -3

In [42]:
class NumpyEncoder(json.JSONEncoder):
    """ Special json encoder for numpy types """
    def default(self, obj):
        if isinstance(obj, np.integer):
            return int(obj)
        elif isinstance(obj, np.floating):
            return float(obj)
        elif isinstance(obj, np.ndarray):
            return obj.tolist()
        return json.JSONEncoder.default(self, obj)

In [43]:
with open("/home/colin/wbc_data_2021.json", 'w') as fp:
    json.dump(output_data, fp,cls=NumpyEncoder)

In [44]:
output_data

{'10051439110': {'10051439110_125.jpg': {'continous': array([-4.611344 , -3.0294473, -4.606042 , -7.443936 , -1.026741 ,
          -7.8839903, -5.784404 , -1.627895 , -9.26863  ], dtype=float32),
   'discrete': 4,
   'type': 'ig',
   'label': 0},
  '10051439110_064.jpg': {'continous': array([-2.0361032 , -2.3554945 , -2.8571608 , -9.557758  , -0.6017902 ,
          -5.1570897 , -5.92108   ,  0.41264394, -5.753858  ], dtype=float32),
   'discrete': 7,
   'type': 'neutrophil',
   'label': 0},
  '10051439110_078.jpg': {'continous': array([-5.283759 , -2.7873263, -4.200277 , -6.2626114, -3.2843263,
          -3.223605 , -5.778183 , -4.6148067, -3.0453045], dtype=float32),
   'discrete': 1,
   'type': 'eosinophil',
   'label': 0},
  '10051439110_014.jpg': {'continous': array([-3.005165 , -2.1253734, -3.5173342, -8.7852745, -1.6150495,
          -4.4838724, -6.356637 , -1.8168248, -9.832097 ], dtype=float32),
   'discrete': 4,
   'type': 'ig',
   'label': 0},
  '10051439110_120.jpg': {'conti

In [24]:
np.argmax(preds)

7